In [3]:
from Bio.PDB import *
import numpy as np
import pandas as pd

parser=PDBParser()
structure=parser.get_structure('ComplexI', '5xtd.pdb')
chains=structure[0]

/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain A is discontinuous at line 67914.
  warnings.warn(
/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain B is discontinuous at line 67953.
  warnings.warn(
/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain C is discontinuous at line 68021.
  warnings.warn(
/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain E is discontinuous at line 68029.
  warnings.warn(
/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain J is discontinuous at line 68064.
  warnings.warn(
/home/filippo/.local/lib/python3.10/site-packages/Bio/PDB/StructureBuilder.py:89: PDBConstructionWarning: WARNING: Chain M is discontinuous 

In [ ]:
# just to keep in mind
# ppb=PPBuilder()
# pp_list=ppb.build_peptides(chains["A"])
# for pp in pp_list:
#     print(pp)

# pp=pp_list[0]

<Polypeptide start=27 end=457>


In [101]:
# function to establish if a residue is in the membrane, intermembrane or matrix space
# 14.7 and -14.7 are the coordinates of the planes that model the membranes
def find_location (coord):
    z=coord[2]
    if z>=-14.7 and z<=14.7:
        return "membrane"
    elif z>14.7:
        return "intermembrane"
    else:
        return "matrix"

In [ ]:
# dictionary of mitochondrial protein with coordinates of CA atoms
mt_pp_dic={}

chain2protein = {
    "s": "MT-ND1",
    "i": "MT-ND2",
    "j": "MT-ND3",
    "r": "MT-ND4",
    "k": "MT-ND4L",
    "l": "MT-ND5",
    "m": "MT-ND6"
}

for chain_id in chain2protein.keys():
        protein_name = chain2protein[chain_id]
        mt_pp_dic[protein_name] = {}
        for res in chains[chain_id]:
                if res.id[0]==" ":
                        mt_pp_dic[protein_name][res.id[1]] = (res["CA"].coord, find_location(res["CA"].coord))

In [105]:
# read the df containing variations produced with the R script 
var_df=pd.read_csv("../mt_var_01")
# extract only variations related to complexI
cI_var=var_df[var_df["SYMBOL"].isin(chain2protein.values())]

In [127]:
locations=[]
for i, row in cI_var.iterrows():
    locations.append(mt_pp_dic[row["SYMBOL"]][row["Protein_position"]][1])
cI_var["Location"]=locations
    

/tmp/ipykernel_5511/4067281739.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cI_var["Location"]=locations


In [185]:
# count number of aminoacid per location per protein
# for normalisation

dic_count={"MT-ND1": [0,0,0],
"MT-ND2": [0,0,0],
"MT-ND3":[0,0,0],
"MT-ND4":[0,0,0],
"MT-ND4L":[0,0,0],
"MT-ND5":[0,0,0],
"MT-ND6": [0,0,0]}

for prot_id in chain2protein.values(): 
    for values in mt_pp_dic[prot_id].values():
        if values[1]=="membrane":
            dic_count[prot_id][0]+=1
        elif values[1]=="matrix":
            dic_count[prot_id][1]+=1
        else:
            dic_count[prot_id][2]+=1

# rearrange df and add counts to the cI_var df in order to have 
# everything in one df

count_df=pd.DataFrame(dic_count).transpose()
count_df.columns=["Membrane", "Matrix", "Intermembrane"]
count_df.reset_index(inplace=True)
count_df.rename(columns={'index': 'SYMBOL'}, inplace=True)
# also add the chain for visualization in pymol
protein2chain = {v: k for k, v in chain2protein.items()}
protein2chain = pd.DataFrame(list(protein2chain.items()), columns=['SYMBOL', 'Chain'])
merged_df=pd.merge(cI_var, protein2chain, on='SYMBOL', how='left')
def_df = pd.merge(merged_df, count_df, on='SYMBOL', how='left')

In [ ]:
import pymol_test as mol
mt_chains=["s","i", "j", "r", "k", "l", "m"]

In [ ]:
mol.cmd.load("5xtd.pdb")
mol.cmd.spectrum()
mol.cmd.select("nuc_sub", "not chain " + "+".join(mt_chains))
mol.cmd.set("cartoon_transparency", 0.7, "nuc_sub")


NameError: name 'mol' is not defined

In [6]:
data=pd.read_csv("complexI.csv")

In [8]:
data

Unnamed: 0  SYMBOL  Protein_position    AF_hom  REF  ALT  Gr_score  \
0            0  MT-ND1                67  0.019779  Thr  Ala        58   
1            1  MT-ND1                81  0.022346  Ile  Val        29   
2            2  MT-ND1               229  0.011448  Thr  Met        81   
3            3  MT-ND1               273  0.013275  Ile  Val        29   
4            4  MT-ND1               304  0.117561  Tyr  His        83   
5            5  MT-ND2               100  0.014041  Met  Val        21   
6            6  MT-ND2               119  0.047746  Thr  Ala        58   
7            7  MT-ND2               150  0.057541  Asn  Asp        23   
8            8  MT-ND2               193  0.043303  Val  Ile        29   
9            9  MT-ND2               237  0.010687  Leu  Met        15   
10          10  MT-ND2               265  0.010406  Ala  Thr        58   
11          11  MT-ND2               288  0.013202  Leu  Ile         5   
12          12  MT-ND2               325  0.014839  Phe  Leu        22   
13          13  MT-ND2               331  0.053983  Ala  Thr        58   
14          14  MT-ND3                10  0.021211  Asn  Asp        23   
15          15  MT-ND3                88  0.018964  Val  Ala        64   
16          16  MT-ND3               114  0.418480  Thr  Ala        58   
17          17  MT-ND4                86  0.018755  Ser  Asn        46   
18          18  MT-ND4               140  0.021533  Pro  Ser        74   
19          19  MT-ND5               257  0.127497  Ile  Val        29   
20          20  MT-ND5               314  0.011681  Met  Val        21   
21          21  MT-ND5               434  0.011394  Gln  Arg        43   
22          22  MT-ND5               458  0.075637  Ala  Thr        58   
23          23  MT-ND5               475  0.014946  Ala  Thr        58   
24          24  MT-ND5               482  0.018482  Ile  Val        29   
25          25  MT-ND5               485  0.052812  Tyr  His        83   
26          26  MT-ND5               515  0.023569  Ser  Tyr       144   
27          27  MT-ND5               517  0.018149  Leu  Pro        98   
28          28  MT-ND5               531  0.026941  Ser  Thr        58   
29          29  MT-ND5               533  0.013308  Thr  Met        81   
30          30  MT-ND5               541  0.014764  Gly  Ala        60   
31          31  MT-ND5               544  0.013539  Thr  Ala        58   
32          32  MT-ND5               555  0.027011  Leu  Gln       113   
33          33  MT-ND5               575  0.013149  Ile  Val        29   
34          34  MT-ND6               166  0.054355  Ile  Val        29   
35          35  MT-ND6               119  0.015347  Asn  Ser        46   

         Location Chain  Membrane  Matrix  Intermembrane  
0          matrix     s       192     120              6  
1        membrane     s       192     120              6  
2        membrane     s       192     120              6  
3          matrix     s       192     120              6  
4        membrane     s       192     120              6  
5        membrane     i       233      68             46  
6        membrane     i       233      68             46  
7   intermembrane     i       233      68             46  
8        membrane     i       233      68             46  
9          matrix     i       233      68             46  
10       membrane     i       233      68             46  
11       membrane     i       233      68             46  
12       membrane     i       233      68             46  
13       membrane     i       233      68             46  
14       membrane     j        61      48              6  
15       membrane     j        61      48              6  
16         matrix     j        61      48              6  
17         matrix     r       295      85             79  
18         matrix     r       295      85             79  
19       membrane     l       391     148             64  
20       membrane     l   

In [24]:
data.groupby("Chain")["Protein_position"].apply(list)

Chain
i        [100, 119, 150, 193, 237, 265, 288, 325, 331]
j                                        [10, 88, 114]
l    [257, 314, 434, 458, 475, 482, 485, 515, 517, ...
m                                           [166, 119]
r                                            [86, 140]
s                              [67, 81, 229, 273, 304]
Name: Protein_position, dtype: object

In [30]:
" ".join(str(v) for v in data["Protein_position"][data["Chain"]=="s"].to_list())

'67 81 229 273 304'